In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
# Step 1: Install required libraries and exiftool
!pip install Pillow imageio[ffmpeg] datasets pandas
!apt-get update && apt-get install -y libimage-exiftool-perl

# Step 2: Import required libraries
import os
import glob
import subprocess
from PIL import Image
import imageio.v3 as iio
import pandas as pd
from datasets import Dataset, Features, Image as HFImage, Value
from google.colab import drive

In [ ]:
# Step 3: Mount Google Drive
drive.mount('/content/drive')
output_dir = '/content/drive/My Drive/exif_dataset' #@param {type:'string'}

# Step 4: Define function to extract metadata using exiftool
def get_exif_data(image_path):
    try:
        # Run exiftool to extract all metadata as JSON
        result = subprocess.run(
            ['exiftool', '-j', image_path],
            stdout=subprocess.PIPE,
            stderr=subprocess.PIPE,
            text=True,
            check=True
        )
        # Parse JSON output (exiftool -j returns a list of dictionaries)
        metadata = eval(result.stdout)[0]  # First item in the list
        return metadata
    except subprocess.CalledProcessError as e:
        print(f"exiftool error for {image_path}: {e.stderr}")
        return {"Error": f"exiftool failed: {str(e)}"}
    except Exception as e:
        return {"Error": f"Failed to read metadata: {str(e)}"}

# Step 5: Define function to convert image to WebM
def convert_to_webm(image_path, output_path):
    try:
        img = iio.imread(image_path)
        iio.imwrite(output_path, img, codec='vp8', fps=1, quality=8)
        return True
    except Exception as e:
        print(f"Error converting {image_path} to WebM: {str(e)}")
        return False

# Step 6: Collect ALL images from /content/
image_dir = "/content/"
image_extensions = ["*.jpg", "*.jpeg", "*.png"]
image_paths = []
for ext in image_extensions:
    image_paths.extend(glob.glob(os.path.join(image_dir, ext)))

if not image_paths:
    print("No images found in /content/")
else:
    # Step 7: Process all images to collect metadata keys and data
    images = []
    webm_paths = []
    metadata_list = []
    all_metadata_keys = set()

    for img_path in image_paths:
        print(f"\nProcessing {img_path}:")

        # Load image
        try:
            img = Image.open(img_path).convert('RGB')
        except Exception as e:
            print(f"Error loading image {img_path}: {str(e)}")
            continue

        # Extract metadata with exiftool
        metadata = get_exif_data(img_path)
        print("Metadata (via exiftool):")
        for key, value in metadata.items():
            print(f"  {key}: {value}")
            all_metadata_keys.add(key)  # Collect unique metadata keys

        # Convert to WebM
        webm_path = os.path.splitext(img_path)[0] + ".webm"
        if convert_to_webm(img_path, webm_path):
            print(f"  Saved WebM: {webm_path}")
            images.append(img)
            webm_paths.append(webm_path)
            metadata_list.append(metadata)
        else:
            print(f"  Skipped WebM conversion for {img_path}")
            continue

    # Step 8: Check if any images were processed
    if not images:
        print("No images were successfully processed.")
    else:
        # Step 9: Prepare dataset dictionary with separate columns for each metadata key
        data_dict = {'image': images, 'webm_path': webm_paths}

        # Initialize columns for each metadata key with None
        for key in all_metadata_keys:
            data_dict[key] = [None] * len(images)

        # Populate metadata values
        for i, metadata in enumerate(metadata_list):
            for key, value in metadata.items():
                data_dict[key][i] = str(value)  # Convert values to strings

        # Step 10: Define dataset features
        features = Features({
            'image': HFImage(),
            'webm_path': Value("string"),
            **{key: Value("string") for key in all_metadata_keys}  # Dynamic columns for metadata keys
        })

        # Step 11: Create Hugging Face Dataset
        dataset = Dataset.from_dict(data_dict, features=features)

        # Step 12: Verify the dataset
        print("\nDataset Summary:")
        print(dataset)
        if len(dataset) > 0:
            print("\nExample of accessing first item:")
            print("WebM Path:", dataset['webm_path'][0])
            print("Image type:", type(dataset['image'][0]))
            print("Image size:", dataset['image'][0].size)
            print("Metadata columns (first item):")
            for key in all_metadata_keys:
                if dataset[key][0] is not None:
                    print(f"  {key}: {dataset[key][0]}")

        # Step 13: Save dataset to Google Drive
        try:
            os.makedirs(output_dir, exist_ok=True)
            dataset.save_to_disk(output_dir)
            print(f"\nDataset saved to {output_dir}")
        except Exception as e:
            print(f"Error saving dataset to Google Drive: {str(e)}")

In [ ]:
#@markdown Create a new dataset with 'image' and 'text' from the original dataset


# Step 14: Import required libraries
from datasets import Dataset, load_from_disk, Image as HFImage, Value
import json
from PIL import Image
import io

# Step 15: Define the path to the original dataset on Google Drive
dataset_path = '/content/drive/MyDrive/exif_dataset'  #@param {type:'string'}

# Step 16: Load the original dataset
try:
    dataset = load_from_disk(dataset_path)
    print("Original dataset loaded successfully!")
except Exception as e:
    print(f"Error loading dataset: {e}")
    raise

# Step 17: Function to extract 'text' from the 'Prompt' dictionary
def extract_text_from_prompt(prompt):
    try:
        # Parse the prompt (assuming it's a string representation of a dictionary)
        # Safely handle cases where prompt might not be a string or valid JSON
        if isinstance(prompt, str):
            try:
                prompt_dict = json.loads(prompt)
            except json.JSONDecodeError:
                # Handle cases where the string is not valid JSON
                print(f"Warning: Could not parse JSON from prompt string: {prompt[:100]}...") # Print a snippet
                return ""
        elif isinstance(prompt, dict):
            prompt_dict = prompt
        else:
            # Handle cases where prompt is not a string or dict
            print(f"Warning: Unexpected prompt type: {type(prompt)}")
            return ""

        # Look for the 'CLIPTextEncode' node with the main text description
        for node_key, node_data in prompt_dict.items():
            if isinstance(node_data, dict) and node_data.get('class_type') == 'CLIPTextEncode' and 'inputs' in node_data and 'text' in node_data['inputs']:
                return str(node_data['inputs']['text']) # Ensure text is a string
        return ""  # Return empty string if no valid text is found
    except Exception as e:
        print(f"Error processing prompt: {e}")
        return ""

# Step 18: Create lists for the new dataset
new_data = {
    'image': [],
    'text': []
}

# Step 19: Process each item in the dataset
print(f"Processing {len(dataset)} items...")
for i in range(len(dataset)):
    try:
        # Get the image and Prompt field
        image = dataset['image'][i]
        prompt = dataset['Prompt'][i]

        # Extract the text from Prompt
        text = extract_text_from_prompt(prompt)

        # Check if text is empty or contains no letters (a-z)
        if not text.strip():  # Skip if text is empty or only whitespace
            print(f"Skipping item at index {i}: Empty text")
            continue
        if not any(c.isalpha() for c in text.lower()):  # Skip if no letters a-z
            print(f"Skipping item at index {i}: No letters in text: {text[:50]}...")
            continue

        # Convert PIL Image to bytes
        img_byte_arr = io.BytesIO()
        image.save(img_byte_arr, format='PNG')  # Use a common format like PNG
        img_bytes = img_byte_arr.getvalue()

        new_data['image'].append(img_bytes)
        new_data['text'].append(text)

    except Exception as e:
        print(f"Error processing item at index {i}: {e}")
        continue  # Skip this item and continue with the next

# Step 20: Define dataset features with Image type
features = Features({
    'image': HFImage(),
    'text': Value("string")
})

# Step 21: Create a new Hugging Face dataset from the byte data
new_dataset = Dataset.from_dict(new_data, features=features)

# Step 22: Define the path to save the new dataset
new_dataset_path = '/content/drive/MyDrive/to_add_dataset'  #@param {type:'string'}

# Step 23: Save the new dataset
try:
    # Ensure the directory exists
    import os
    os.makedirs(new_dataset_path, exist_ok=True)
    new_dataset.save_to_disk(new_dataset_path)
    print(f"New dataset saved successfully to {new_dataset_path}!")
except Exception as e:
    print(f"Error saving new dataset: {e}")
    raise

# Step 24: Verify the new dataset
print("\nNew dataset info:")
print(new_dataset)

# Step 25: Example of accessing an item in the new dataset
index_to_test = 0  #@param {type:'slider', max:200}
index=index_to_test
if index < len(new_dataset):
    print("\nExample of accessing item at index", index)
    print("Text:", new_dataset['text'][index])
    # When accessing, the Image feature automatically loads the image bytes back into a PIL Image
    print("Image type:", type(new_dataset['image'][index]))
    print("Image size:", new_dataset['image'][index].size)

    # Optional: Display the image
    display(new_dataset['image'][index])
else:
    print(f"\nIndex {index} is out of bounds for the new dataset (size {len(new_dataset)}).")

In [ ]:
#@markdown Merge the two datasets into one

# Step 1: Import required libraries
from datasets import load_from_disk, concatenate_datasets
from google.colab import drive

# Step 2: Mount Google Drive (only needed in Google Colab)
drive.mount('/content/drive')

# Step 3: Define paths for the datasets
dataset1_path = '/content/drive/MyDrive/my_datasetv2' #@param {type:'string'}
dataset2_path = '/content/drive/MyDrive/to_add_dataset' #@param {type:'string'}
merged_dataset_path = '/content/drive/MyDrive/my_datasetv3'  #@param {type:'string'}

# Step 4: Load the datasets
try:
    dataset1 = load_from_disk(dataset1_path)
    dataset2 = load_from_disk(dataset2_path)
    print("Datasets loaded successfully!")
except Exception as e:
    print(f"Error loading datasets: {e}")
    raise

# Step 5: Verify the datasets
print("Dataset 1:", dataset1)
print("Dataset 2:", dataset2)

# Step 6: Merge the datasets
try:
    dataset = concatenate_datasets([dataset1, dataset2])
    print("Datasets merged successfully!")
except Exception as e:
    print(f"Error merging datasets: {e}")
    raise

# Step 7: Verify the merged dataset
print("Merged Dataset:", dataset)
dataset1=''
dataset2=''
# Step 8: Save the merged dataset to Google Drive
try:
    dataset.save_to_disk(merged_dataset_path)
    print(f"Merged dataset saved successfully to {merged_dataset_path}")
except Exception as e:
    print(f"Error saving merged dataset: {e}")
    raise

# Step 9: Optional - Verify the saved dataset by loading it back
try:
    dataset = load_from_disk(merged_dataset_path)
    print("Saved merged dataset loaded successfully for verification:")
    print(dataset)
except Exception as e:
    print(f"Error loading saved merged dataset: {e}")
    raise